In [1]:


# %%
from pathlib import Path
import os

path = Path().resolve()
root_path = str(path).split('notebooks')[0]
os.chdir(root_path)


In [2]:
from shared import *
import plotly.express as px
from models.system_model_v3.model.params.init import eth_price_df
from models.system_model_v3.model.state_variables.init import state_variables
from models.system_model_v3.model.params.init import params
from cadCAD_tools import profile_run



In [3]:


state_variables.update({})

params_update = {
    'controller_enabled': [True],
    'kp': [2e-07],  # proportional term for the stability controller: units 1/USD
    # integral term for the stability controller: units 1/(USD*seconds)
    'ki': [-5e-09],
}

params.update(params_update)
SIMULATION_TIMESTEPS = len(eth_price_df) - 1
# SIMULATION_TIMESTEPS = 1000
system_simulation = ConfigWrapper(system_model_v3, T=range(
    SIMULATION_TIMESTEPS), M=params, initial_state=state_variables)
del configs[:]  # Clear any prior configs


df = profile_run(state_variables,
                 params,
                 system_simulation.partial_state_update_blocks,
                 SIMULATION_TIMESTEPS,
                 system_simulation.N,
                 use_label=True,
                 assign_params=False)


Initializing configurations: 100%|██████████| 1/1 [00:00<00:00, 11.33it/s]
                  ___________    ____
  ________ __ ___/ / ____/   |  / __ \
 / ___/ __` / __  / /   / /| | / / / /
/ /__/ /_/ / /_/ / /___/ ___ |/ /_/ /
\___/\__,_/\__,_/\____/_/  |_/_____/
by cadCAD

Execution Mode: local_proc
Configuration Count: 1
Dimensions of the first simulation: (Timesteps, Params, Runs, Vars) = (8758, 34, 1, 44)
Execution Method: local_simulations
SimIDs   : [0]
SubsetIDs: [0]
Ns       : [0]
ExpIDs   : [0]
Execution Mode: single_threaded
list index out of range
list index out of range
list index out of range

Flattening results:   0%|          | 1/324047 [00:00<6:17:11, 14.32it/s]
Total execution time: 1517.14s


In [4]:
from cadCAD_tools.profiling.visualizations import visualize_elapsed_time_per_ts

visualize_elapsed_time_per_ts(df)

In [5]:
from cadCAD_tools.profiling.visualizations import visualize_substep_impact

visualize_substep_impact(df.query('timestep > 800'), relative=True)

100%|██████████| 7958/7958 [07:31<00:00, 17.63it/s]


In [6]:
visualize_substep_impact(df.query('timestep > 8000'), relative=True)


100%|██████████| 758/758 [00:40<00:00, 18.66it/s]


In [7]:
visualize_elapsed_time_per_ts(df, relative=True)
